In [18]:
import pandas as pd
import numpy as np
from scipy import special
import itertools
from datetime import timedelta

In [19]:
fraude_df = pd.read_csv('Fraud_Data.csv', header=0)
fraude_df.head()

id             cadastro               compra  valor id_dispositivo  \
0   22058  2015-02-24 22:55:49  2015-04-18 02:47:11     34  QVPSPJUOCKZAR   
1  333320  2015-06-07 20:39:50  2015-06-08 01:38:54     16  EOGFQPIZPYXFZ   
2    1359  2015-01-01 18:52:44  2015-01-01 18:52:45     15  YSSKYOSJHPPLJ   
3  150084  2015-04-28 21:13:25  2015-05-04 13:54:50     44  ATGTXKYKUDUQN   
4  221365  2015-07-21 07:09:52  2015-09-09 18:40:53     39  NAUITBZFJKHWW   

  fonte browser genero  idade            ip  fraude  
0   SEO  Chrome      M     39  7.327584e+08       0  
1   Ads  Chrome      F     53  3.503114e+08       0  
2   SEO   Opera      M     53  2.621474e+09       1  
3   SEO  Safari      M     41  3.840542e+09       0  
4   Ads  Safari      M     45  4.155831e+08       0

In [20]:
ISP_df = pd.read_csv('IpAddress_to_Country.csv', header=0)
ISP_df.head()

limite_inferior_ip  limite_superior_ip       pais
0          16777216.0            16777471  Australia
1          16777472.0            16777727      China
2          16777728.0            16778239      China
3          16778240.0            16779263  Australia
4          16779264.0            16781311      China

In [21]:
fraude_df.isnull().sum()

id                0
cadastro          0
compra            0
valor             0
id_dispositivo    0
fonte             0
browser           0
genero            0
idade             0
ip                0
fraude            0
dtype: int64

In [22]:
fraude_df.describe()

id          valor          idade            ip  \
count  151112.000000  151112.000000  151112.000000  1.511120e+05   
mean   200171.040970      36.935372      33.140704  2.152145e+09   
std    115369.285024      18.322762       8.617733  1.248497e+09   
min         2.000000       9.000000      18.000000  5.209350e+04   
25%    100642.500000      22.000000      27.000000  1.085934e+09   
50%    199958.000000      35.000000      33.000000  2.154770e+09   
75%    300054.000000      49.000000      39.000000  3.243258e+09   
max    400000.000000     154.000000      76.000000  4.294850e+09   

              fraude  
count  151112.000000  
mean        0.093646  
std         0.291336  
min         0.000000  
25%         0.000000  
50%         0.000000  
75%         0.000000  
max         1.000000

In [23]:
ISP_df.dtypes

limite_inferior_ip    float64
limite_superior_ip      int64
pais                   object
dtype: object

In [24]:
ISP_df['limite_inferior_ip'] = ISP_df['limite_inferior_ip'].astype(int)

In [25]:
ISP_df.isnull().sum()

limite_inferior_ip    0
limite_superior_ip    0
pais                  0
dtype: int64

In [26]:
ISP_df.describe()

limite_inferior_ip  limite_superior_ip
count        1.388460e+05        1.388460e+05
mean        -1.214785e+09        2.724557e+09
std          1.563396e+09        8.974979e+08
min         -2.147484e+09        1.677747e+07
25%         -2.147484e+09        1.920008e+09
50%         -2.147484e+09        3.230888e+09
75%          5.228780e+08        3.350466e+09
max          2.113929e+09        3.758096e+09

In [27]:
def isp_counts(isp):
    pais = ISP_df[(ISP_df.limite_inferior_ip <= isp) & (ISP_df.limite_superior_ip >= isp)].pais
    if pais.shape[0] == 1:
        return print("Único")
    elif pais.shape[0] > 1:
        return print("Vários países")
    elif pais.shape[0] == 0:
        if isp > ISP_df.limite_superior_ip.max():
            return print("Muito grande")
        elif isp < ISP_df.limite_inferior_ip.min():
            return print("Muito pequeno")
        else:
            return print("Faltando")
        
ip_counts = fraude_df.ip.apply(isp_counts)
ip_counts.value_counts()

Vários países
Vários países
Vários países
Muito grande
Vários países
Vários países
Muito grande
Vários países
Vários países
Vários países
Vários países
Muito grande
Muito grande
Vários países
Muito grande
Vários países
Vários países
Vários países
Vários países
Vários países
Muito grande
Muito grande
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Muito grande
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Muito grande
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Muito grande
Vários países
Vários países
Muito grande
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vários países
Vár

Series([], Name: ip, dtype: int64)

In [28]:
def ip_para_pais(ip):
    tmp = ISP_df[(ISP_df.limite_inferior_ip <= ip)
                & (ISP_df.limite_superior_ip >= ip)].pais
    if tmp.shape[0] == 1:
        return tmp.iloc[0]
    elif tmp.shape[0] < 1:
        return print("Faltando")
    elif tmp.shape[0] > 1:
        return print("Erro")
    
fraude_df["pais"] = fraude_df.ip.apply(ip_para_pais)

Erro
Erro
Erro
Faltando
Erro
Erro
Faltando
Erro
Erro
Erro
Erro
Faltando
Faltando
Erro
Faltando
Erro
Erro
Erro
Erro
Erro
Faltando
Faltando
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Faltando
Erro
Erro
Erro
Erro
Erro
Erro
Faltando
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Faltando
Erro
Erro
Faltando
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Faltando
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Faltando
Erro
Erro
Erro
Erro
Erro
Faltando
Faltando
Erro
Erro
Erro
Faltando
Erro
Faltando
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Faltando
Erro
Erro
Erro
Faltando
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Faltando
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Faltando
Erro
Erro
Erro
Erro
Faltando
Erro
Faltando
Faltando
Erro
Erro
Erro
Erro
Erro
Faltando
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Erro
Faltando
E

In [31]:
fraude_df.head()

id             cadastro               compra  valor id_dispositivo  \
0   22058  2015-02-24 22:55:49  2015-04-18 02:47:11     34  QVPSPJUOCKZAR   
1  333320  2015-06-07 20:39:50  2015-06-08 01:38:54     16  EOGFQPIZPYXFZ   
2    1359  2015-01-01 18:52:44  2015-01-01 18:52:45     15  YSSKYOSJHPPLJ   
3  150084  2015-04-28 21:13:25  2015-05-04 13:54:50     44  ATGTXKYKUDUQN   
4  221365  2015-07-21 07:09:52  2015-09-09 18:40:53     39  NAUITBZFJKHWW   

  fonte browser genero  idade            ip  fraude  pais  
0   SEO  Chrome      M     39  7.327584e+08       0  None  
1   Ads  Chrome      F     53  3.503114e+08       0  None  
2   SEO   Opera      M     53  2.621474e+09       1  None  
3   SEO  Safari      M     41  3.840542e+09       0  None  
4   Ads  Safari      M     45  4.155831e+08       0  None

In [30]:
fraude_df.to_csv('Dados_fraude_com_pais.csv', index=False)

In [14]:
fraude_df = pd.read_csv('Dados_fraude_com_pais.csv', header=0)
fraude_df.head()

id             cadastro               compra  valor id_dispositivo  \
0   22058  2015-02-24 22:55:49  2015-04-18 02:47:11     34  QVPSPJUOCKZAR   
1  333320  2015-06-07 20:39:50  2015-06-08 01:38:54     16  EOGFQPIZPYXFZ   
2    1359  2015-01-01 18:52:44  2015-01-01 18:52:45     15  YSSKYOSJHPPLJ   
3  150084  2015-04-28 21:13:25  2015-05-04 13:54:50     44  ATGTXKYKUDUQN   
4  221365  2015-07-21 07:09:52  2015-09-09 18:40:53     39  NAUITBZFJKHWW   

  fonte browser genero  idade            ip  fraude  pais  
0   SEO  Chrome      M     39  7.327584e+08       0   NaN  
1   Ads  Chrome      F     53  3.503114e+08       0   NaN  
2   SEO   Opera      M     53  2.621474e+09       1   NaN  
3   SEO  Safari      M     41  3.840542e+09       0   NaN  
4   Ads  Safari      M     45  4.155831e+08       0   NaN

In [34]:
fraude_df.loc[fraude_df.pais != np.nan]

id             cadastro               compra  valor  \
0        22058  2015-02-24 22:55:49  2015-04-18 02:47:11     34   
1       333320  2015-06-07 20:39:50  2015-06-08 01:38:54     16   
2         1359  2015-01-01 18:52:44  2015-01-01 18:52:45     15   
3       150084  2015-04-28 21:13:25  2015-05-04 13:54:50     44   
4       221365  2015-07-21 07:09:52  2015-09-09 18:40:53     39   
...        ...                  ...                  ...    ...   
151107  345170  2015-01-27 03:03:34  2015-03-29 00:30:47     43   
151108  274471  2015-05-15 17:43:29  2015-05-26 12:24:39     35   
151109  368416  2015-03-03 23:07:31  2015-05-20 07:07:47     40   
151110  207709  2015-07-09 20:06:07  2015-09-07 09:34:46     46   
151111  138208  2015-06-10 07:02:20  2015-07-21 02:03:53     20   

       id_dispositivo   fonte browser genero  idade            ip  fraude  \
0       QVPSPJUOCKZAR     SEO  Chrome      M     39  7.327584e+08       0   
1       EOGFQPIZPYXFZ     Ads  Chrome      F     53  3.503114e+08       0   
2       YSSKYOSJHPPLJ     SEO   Opera      M     53  2.621474e+09       1   
3       ATGTXKYKUDUQN     SEO  Safari      M     41  3.840542e+09       0   
4       NAUITBZFJKHWW     Ads  Safari      M     45  4.155831e+08       0   
...               ...     ...     ...    ...    ...           ...     ...   
151107  XPSKTWGPWINLR     SEO  Chrome      M     28  3.451155e+09       1   
151108  LYSFABUCPCGBA     SEO  Safari      M     32  2.439047e+09       0   
151109  MEQHCSJUBRBFE     SEO      IE      F     26  2.748471e+09       0   
151110  CMCXFGRHYSTVJ     SEO  Chrome      M     37  3.601175e+09       0   
151111  ZINIADFCLHYPG  Direct      IE      M     38  4.103825e+09       0   

        pais  
0       None  
1       None  
2       None  
3       None  
4       None  
...      ...  
151107  None  
151108  None  
151109  None  
151110  None  
151111  None  

[151112 rows x 12 columns]